In [1]:
%pip install numpy
%pip install scipy
%pip install plotly

import numpy as np
from scipy.optimize import minimize_scalar
import plotly.graph_objects as go

# Constants in SI units
Trs = 298.15  # Reference temperature in K
a1 = 9.48*4.184  # J/mol
b1 = 0.00914*4.184  # J/(mol*K)
c1 = -6.4e-7*4.184  # J/(mol*K^2)
R = 8.314  # J/(mol*K)
Tc = 414.48  # K
Pc = 6.8e6  # Pa
w = 0.215  # dimensionless
a = 0.45724 * (R**2 * Tc**2) / Pc  # Pa * m^6 / mol^2
b = 0.07780 * R * Tc / Pc  # m^3 / mol

# Define pressure function
def calculate_pressure(Vm, T):
    k = 0.37464 + 1.54226 * w - 0.26992 * w**2
    alpha = (1 + k * (1 - np.sqrt(T / Tc)))**2
    return (R * T / (Vm - b)) - (a * alpha / (Vm**2 + 2 * b * Vm - b**2))

# Helper functions for a, b calculation
def calc_a(T):
    kappa = 0.37464 + 1.54226 * w - 0.26992 * w**2
    return 0.45724 * R**2 * Tc**2 / Pc * (1 + kappa * (1 - np.sqrt(T / Tc)))**2

def calc_b():
    return 0.07780 * R * Tc / Pc

# Solve cubic for Z
def solve_cubic(A, B):
    coeffs = [1, -(1 - B), A - 3 * B**2 - 2 * B, -(A * B - B**2 - B**3)]
    roots = np.roots(coeffs)
    return np.real(roots[np.isreal(roots)])   # Only real roots

# Calculate properties
def calculate_properties(T, P):
    A = calc_a(T) * P / (R * T)**2
    B = calc_b() * P / (R * T)
    Z_values = solve_cubic(A, B)
    Z1, Z3 = np.min(Z_values), np.max(Z_values)
    V1 = Z1 * R * T / P  # m^3/mol
    V3 = Z3 * R * T / P  # m^3/mol
    return Z1, Z3, V1, V3

# Integrate using compute_integral (skipping details for now, assume correct)
def compute_integral(P, R, T, a, b, P_min, k=0.001):
    Z1, Z3, V1, V2 = calculate_properties(T, P)
    kappa = 0.37464 + 1.54226 * w - 0.26992 * w**2
    alpha = (1 + kappa * (1 - np.sqrt(T / Tc)))**2
    a = a * alpha
    def integral_function(V):
        term1 = R * T * np.log(abs(V - b))
        term2 = -(a / (2 * b * np.sqrt(2))) * np.log(abs((V + b - b * np.sqrt(2)) / (V + b + b * np.sqrt(2))))
        return term1 + term2
    integral_value = integral_function(V2) - integral_function(V1)
    while P > P_min:
        residual = integral_value - (V2 - V1) * P
        if abs(residual) < k:
            return P
        P -= 1  
    print("Stopped as P reached P_min without convergence.")
    return P

# Initialize plot
fig = go.Figure()

# Define temperature range
temperature_list = np.arange(314.48, 500, 20)
pressure_values = np.linspace(1e5, 1e7, 10000)     # Adjusted pressure range in Pa

# Loop over each temperature
for T in temperature_list:
    result = minimize_scalar(lambda Vm: -calculate_pressure(Vm, T), bounds=(0.00005, 0.01), method='bounded')
    result_min = minimize_scalar(lambda Vm: calculate_pressure(Vm, T), bounds=(0.00005, 0.01), method='bounded')
    V_max = result.x
    P_max = -result.fun
    V_min = result_min.x
    P_min = result_min.fun
    P_sat = compute_integral(P_max, R, T, a, b, P_min)

    # Volume values for plotting
    V_values = []
    for P in pressure_values:
        Z1, Z3, V1, V3 = calculate_properties(T, P)
        if np.isclose(V1, V3, rtol=1e-4):
            V_values.append(V1)
        elif P > P_sat:
            V_values.append(V1)
        else:
            V_values.append(V3)

    # Add to plot
    fig.add_trace(go.Scatter(x=np.log(V_values), y=np.log(pressure_values), mode='lines', name=f'T = {T} K'))

# Plot labels
fig.update_layout(
    title='Volume vs Pressure for Formaldehyde at Different Temperatures with log scale',
    xaxis_title='Volume (m^3/mol)',
    yaxis_title='Pressure (Pa)',
    legend_title='Temperature'
)
fig.show()



[notice] A new release of pip is available: 24.0 -> 24.3.1
[notice] To update, run: python.exe -m pip install --upgrade pip



[notice] A new release of pip is available: 24.0 -> 24.3.1
[notice] To update, run: python.exe -m pip install --upgrade pip


Note: you may need to restart the kernel to use updated packages.



[notice] A new release of pip is available: 24.0 -> 24.3.1
[notice] To update, run: python.exe -m pip install --upgrade pip


Stopped as P reached P_min without convergence.
Stopped as P reached P_min without convergence.
